In [74]:
import numpy as np
import pandas as pd
from stocktrends import Renko
import statsmodels.api as sm
import yfinance as yf
import datetime as dt
import copy
import time

def ATR(DF,n):
    "function to calculate True Range and Average True Range"
    df = DF.copy()
    df['H-L']=abs(df['High']-df['Low'])
    df['H-PC']=abs(df['High']-df['Close'].shift(1))
    df['L-PC']=abs(df['Low']-df['Close'].shift(1))
    df['TR']=df[['H-L','H-PC','L-PC']].max(axis=1,skipna=False)
    df['ATR'] = df['TR'].rolling(n).mean()
    #df['ATR'] = df['TR'].ewm(span=n,adjust=False,min_periods=n).mean()
    df2 = df.drop(['H-L','H-PC','L-PC'],axis=1)
    return df2['ATR']

def CAGR(DF):
    "function to calculate the Cumulative Annual Growth Rate of a trading strategy"
    df = DF.copy()
    df["cum_return"] = (1 + df["ret"]).cumprod()
    n = len(df)/(252*78)
    CAGR = (df["cum_return"].tolist()[-1])**(1/n) - 1
    return CAGR

def volatility(DF):
    "function to calculate annualized volatility of a trading strategy"
    df = DF.copy()
    vol = df["ret"].std() * np.sqrt(252*78)
    return vol

def sharpe(DF,rf):
    "function to calculate sharpe ratio ; rf is the risk free rate"
    df = DF.copy()
    sr = (CAGR(df) - rf)/volatility(df)
    return sr
    

def max_dd(DF):
    "function to calculate max drawdown"
    df = DF.copy()
    df["cum_return"] = (1 + df["ret"]).cumprod()
    df["cum_roll_max"] = df["cum_return"].cummax()
    df["drawdown"] = df["cum_roll_max"] - df["cum_return"]
    df["drawdown_pct"] = df["drawdown"]/df["cum_roll_max"]
    max_dd = df["drawdown_pct"].max()
    return max_dd

def renko_DF(DF):
    "function to convert ohlc data into renko bricks"
    df = DF.copy()
    df.reset_index(inplace=True)
    df = df.iloc[:,[0,1,2,3,4,5]]
    df.columns = ["date","open","high","low","close","volume"]
    df2 = Renko(df)
    #df2.brick_size = max(0.5,round(ATR(DF,120)["ATR"][-1],0))
    df2.brick_size = max(0.5,round(ATR(DF, 120)["ATR"][-1], 0))       
    print(df2.brick_size)
    renko_df = df2.get_ohlc_data()
    renko_df["bar_num"] = np.where(renko_df["uptrend"]==True,1,np.where(renko_df["uptrend"]==False,-1,0))
    for i in range(1,len(renko_df["bar_num"])):
        if renko_df["bar_num"][i]>0 and renko_df["bar_num"][i-1]>0:
            renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
        elif renko_df["bar_num"][i]<0 and renko_df["bar_num"][i-1]<0:
            renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
    renko_df.drop_duplicates(subset="date",keep="last",inplace=True)
    return renko_df

def download_intraday_data(tickers, start, end, interval='5m'):
    """
    Download historical OHLC data for a list of tickers.

    :param tickers: List of ticker symbols.
    :param start: Start date for the data.
    :param end: End date for the data.
    :param interval: Data interval. Default is '1mo' for monthly data.
    :return: Dictionary with tickers as keys and OHLC data as values.
    """
    ohlc_data = {}
    for ticker in tickers:
        try:
            data = yf.download(ticker, start, end, interval=interval)
            if not data.empty:
                ohlc_data[ticker] = data.dropna(how="all")
        except Exception as e:
            print(f"Failed to download data for {ticker}: {e}")
    return ohlc_data

def OBV(DF):
    """function to calculate On Balance Volume"""
    df = DF.copy()
    df['daily_ret'] = df['Close'].pct_change()
    df['direction'] = np.where(df['daily_ret']>=0,1,-1)
    df['direction'][0] = 0
    df['vol_adj'] = df['Volume'] * df['direction']
    df['obv'] = df['vol_adj'].cumsum()
    return df['obv']

def slope(ser,n):
    "function to calculate the slope of n consecutive points on a plot"
    slopes = [i*0 for i in range(n-1)]
    for i in range(n,len(ser)+1):
        y = ser[i-n:i]
        x = np.array(range(n))
        y_scaled = (y - y.min())/(y.max() - y.min())
        x_scaled = (x - x.min())/(x.max() - x.min())
        x_scaled = sm.add_constant(x_scaled)
        model = sm.OLS(y_scaled,x_scaled)
        results = model.fit()
        slopes.append(results.params[-1])
    slope_angle = (np.rad2deg(np.arctan(np.array(slopes))))
    return np.array(slope_angle)

def MACD(DF,a,b,c):
    """function to calculate MACD
       typical values a = 12; b =26, c =9"""
    df = DF.copy()
    df["MA_Fast"]=df["Close"].ewm(span=a,min_periods=a).mean()
    df["MA_Slow"]=df["Close"].ewm(span=b,min_periods=b).mean()
    df["MACD"]=df["MA_Fast"]-df["MA_Slow"]
    df["Signal"]=df["MACD"].ewm(span=c,min_periods=c).mean()
    df.dropna(inplace=True)
    return (df["MACD"],df["Signal"])

In [75]:
## Downloading Data
### Selecting the stocks traded in terms of value
bhav=pd.read_csv("/Users/alekhsaxena/Downloads/cm03JAN2024bhav.csv")
bhav=bhav.sort_values(by='TOTTRDVAL',ascending=False)
bhav=bhav[0:50]
bhav['ticker']=bhav['SYMBOL']+'.NS'
tickers = bhav['ticker']
tickers

start_date = (dt.datetime.today() - dt.timedelta(30)).date()
end_date = dt.datetime.today().date()
historical_data = download_intraday_data(tickers, start_date, end_date, interval='5m')

for ticker in historical_data.keys():
    historical_data[ticker]=historical_data[ticker].drop('Close',axis=1)
    historical_data[ticker].columns=['Open', 'High', 'Low', 'Close', 'Volume']

[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%*******

In [76]:
def calculate_returns(df):
    # Initialize an empty list to store returns
    returns = [0]

    # Initialize a variable to store the last signal
    last_signal = ""

    for i in range(1, len(df)):
        if last_signal == "":
            returns.append(0)
            if df["High"][i] >= df["roll_max_cp"][i] and df["Volume"][i] > 1.5 * df["roll_max_vol"][i - 1]:
                last_signal = "Buy"
            elif df["Low"][i] <= df["roll_min_cp"][i] and df["Volume"][i] > 1.5 * df["roll_max_vol"][i - 1]:
                last_signal = "Sell"

        elif last_signal == "Buy":
            if df["Low"][i] < df["Close"][i - 1] - df["ATR"][i - 1]:
                last_signal = ""
                returns.append(((df["Close"][i - 1] - df["ATR"][i - 1]) / df["Close"][i - 1]) - 1)
            elif df["Low"][i] <= df["roll_min_cp"][i] and df["Volume"][i] > 1.5 * df["roll_max_vol"][i - 1]:
                last_signal = "Sell"
                returns.append((df["Close"][i] / df["Close"][i - 1]) - 1)
            else:
                returns.append((df["Close"][i] / df["Close"][i - 1]) - 1)

        elif last_signal == "Sell":
            if df["High"][i] > df["Close"][i - 1] + df["ATR"][i - 1]:
                last_signal = ""
                returns.append((df["Close"][i - 1] / (df["Close"][i - 1] + df["ATR"][i - 1])) - 1)
            elif df["High"][i] >= df["roll_max_cp"][i] and df["Volume"][i] > 1.5 * df["roll_max_vol"][i - 1]:
                last_signal = "Buy"
                returns.append((df["Close"][i - 1] / df["Close"][i]) - 1)
            else:
                returns.append((df["Close"][i - 1] / df["Close"][i]) - 1)

    # Add the returns list as a new column to the DataFrame
    df["ret"] = returns


In [110]:
def process_data(historical_data):
    for ticker in historical_data.keys():
        df = historical_data[ticker]
        # Calculating ATR and rolling max/min price and volume
        df["ATR"] = ATR(df, 20)["ATR"]
        df["roll_max_cp"] = df["High"].rolling(20).max()
        df["roll_min_cp"] = df["Low"].rolling(20).min()
        df["roll_max_vol"] = df["Volume"].rolling(20).max()
        df.dropna(inplace=True)

        # Calculating returns
        calculate_returns(df)

        historical_data[ticker] = df

    return historical_data


In [78]:
def calculate_kpis(processed_data):
    cagr = {}
    sharpe_ratios = {}
    max_drawdown = {}
    actual_returns = {}

    for ticker, data in processed_data.items():
        print("Calculating KPIs for", ticker)
        cagr[ticker] = CAGR(data)
        sharpe_ratios[ticker] = sharpe(data, 0.025)
        max_drawdown[ticker] = max_dd(data)
        actual_returns[ticker] = calculate_actual_return(data)

    KPI_df = pd.DataFrame([cagr, sharpe_ratios, max_drawdown, actual_returns], 
                          index=["CAGR", "Sharpe Ratio", "Max Drawdown", "Actual Return"])
    return KPI_df.T

def calculate_actual_return(df):
    df=df.reset_index()
    # Calculate the mean of the 'ret' column
    return (1+df['ret']).prod()

# Example usage
# processed_data = process_data(tickers, start_date, end_date)
# kpi_df = calculate_kpis(processed_data)


In [79]:
processed_data=process_data(historical_data)
kpi_df_breakout = calculate_kpis(processed_data)

Calculating KPIs for ADANIENT.NS
Calculating KPIs for ADANIPORTS.NS
Calculating KPIs for HDFCBANK.NS
Calculating KPIs for ATGL.NS
Calculating KPIs for ICICIBANK.NS
Calculating KPIs for ADANIENSOL.NS
Calculating KPIs for IRCON.NS
Calculating KPIs for ADANIGREEN.NS
Calculating KPIs for RPOWER.NS
Calculating KPIs for RELIANCE.NS
Calculating KPIs for ITC.NS
Calculating KPIs for INFY.NS
Calculating KPIs for AXISBANK.NS
Calculating KPIs for NBCC.NS
Calculating KPIs for BHEL.NS
Calculating KPIs for SPARC.NS
Calculating KPIs for IRFC.NS
Calculating KPIs for ENGINERSIN.NS
Calculating KPIs for IDEA.NS
Calculating KPIs for SBIN.NS
Calculating KPIs for CANBK.NS
Calculating KPIs for YESBANK.NS
Calculating KPIs for BAJAJ-AUTO.NS
Calculating KPIs for RVNL.NS
Calculating KPIs for BANDHANBNK.NS
Calculating KPIs for BIOCON.NS
Calculating KPIs for NATIONALUM.NS
Calculating KPIs for AMBUJACEM.NS
Calculating KPIs for AWL.NS
Calculating KPIs for PNB.NS
Calculating KPIs for KOTAKBANK.NS
Calculating KPIs for 

In [80]:
kpi_df_breakout

CAGR  Sharpe Ratio  Max Drawdown  Actual Return
ADANIENT.NS    0.051386      0.200608      0.043579       1.003972
ADANIPORTS.NS -0.146644     -1.605439      0.035908       0.987533
HDFCBANK.NS   -0.087927     -2.602411      0.020433       0.992745
ATGL.NS       -0.047548     -0.233347      0.079147       0.996153
ICICIBANK.NS  -0.120528     -4.179259      0.015887       0.989891
ADANIENSOL.NS  0.017841     -0.042251      0.037134       1.001400
IRCON.NS      -0.002203     -0.193591      0.033135       0.999826
ADANIGREEN.NS  0.096174      0.399916      0.049385       1.007291
RPOWER.NS      0.337864      1.506935      0.070828       1.023294
RELIANCE.NS    0.099338      1.761048      0.005663       1.007521
ITC.NS        -0.008014     -0.711259      0.013467       0.999364
INFY.NS        0.786084     10.686888      0.010228       1.046955
AXISBANK.NS    0.219753      3.618086      0.007128       1.015839
NBCC.NS        0.620729      2.739075      0.036698       1.038940
BHEL.NS       -0.385524     -3.315891      0.039235       0.962207
SPARC.NS       3.992950     12.781718      0.025009       1.135658
IRFC.NS       -0.404363     -2.070342      0.054071       0.959840
ENGINERSIN.NS  0.344409      1.452585      0.037337       1.023689
IDEA.NS        4.197852     13.745804      0.033396       1.139277
SBIN.NS        0.054257      0.549358      0.020583       1.004189
CANBK.NS       0.397628      3.542528      0.033326       1.026838
YESBANK.NS    -0.597136     -3.860737      0.071713       0.930602
BAJAJ-AUTO.NS  0.446748      4.490893      0.009214       1.029648
RVNL.NS        0.243178      1.469370      0.029676       1.017369
BANDHANBNK.NS -0.257646     -2.732945      0.038093       0.976706
BIOCON.NS      0.778741      5.480099      0.016785       1.046614
NATIONALUM.NS  1.083069      4.576890      0.025204       1.059773
AMBUJACEM.NS  -0.365966     -5.655786      0.040092       0.964595
AWL.NS         1.019743      7.686562      0.023977       1.057188
PNB.NS        -0.119496     -1.346038      0.029934       0.989983
KOTAKBANK.NS  -0.189800     -6.244618      0.016513       0.983487
TATAMOTORS.NS -0.241275     -3.494020      0.037725       0.978393
TCS.NS         0.852250      8.774674      0.009657       1.049972
IRCTC.NS      -0.011984     -0.223338      0.054582       0.999047
TATASTEEL.NS  -0.142534     -2.343697      0.026568       0.987909
HAL.NS        -0.119204     -1.638266      0.016968       0.990009
ALOKINDS.NS   -0.433081     -2.217419      0.101547       0.956095
VEDL.NS        0.361312      3.075080      0.016029       1.024702
RAILTEL.NS     1.504546      8.008785      0.031246       1.075335
PAYTM.NS       0.495336      3.768143      0.015161       1.032342
HINDPETRO.NS   0.527351      3.801096      0.015428       1.034074
MARUTI.NS     -0.159407     -5.759505      0.014228       0.986357
PFC.NS        -0.032105     -0.489962      0.034442       0.997422
ZOMATO.NS      0.239306      2.273694      0.020804       1.017118
COALINDIA.NS   0.582858      5.655501      0.011074       1.036998
BANKBARODA.NS  0.838808      7.580244      0.015326       1.049368
RECLTD.NS      0.478701      3.340984      0.019035       1.031429
WIPRO.NS       0.478347      3.755095      0.016146       1.031409
LT.NS         -0.014906     -1.027519      0.008302       0.998813
NTPC.NS        0.311605      3.064031      0.016707       1.021691

# OBV

In [81]:
import numpy as np
import pandas as pd
from stocktrends import Renko
import statsmodels.api as sm
from alpha_vantage.timeseries import TimeSeries
import copy


def ATR(DF,n):
    "function to calculate True Range and Average True Range"
    df = DF.copy()
    df['H-L']=abs(df['High']-df['Low'])
    df['H-PC']=abs(df['High']-df['Close'].shift(1))
    df['L-PC']=abs(df['Low']-df['Close'].shift(1))
    df['TR']=df[['H-L','H-PC','L-PC']].max(axis=1,skipna=False)
    df['ATR'] = df['TR'].rolling(n).mean()
    #df['ATR'] = df['TR'].ewm(span=n,adjust=False,min_periods=n).mean()
    df2 = df.drop(['H-L','H-PC','L-PC'],axis=1)
    return df2

def slope(ser,n):
    "function to calculate the slope of n consecutive points on a plot"
    slopes = [i*0 for i in range(n-1)]
    for i in range(n,len(ser)+1):
        y = ser[i-n:i]
        x = np.array(range(n))
        y_scaled = (y - y.min())/(y.max() - y.min())
        x_scaled = (x - x.min())/(x.max() - x.min())
        x_scaled = sm.add_constant(x_scaled)
        model = sm.OLS(y_scaled,x_scaled)
        results = model.fit()
        slopes.append(results.params[-1])
    slope_angle = (np.rad2deg(np.arctan(np.array(slopes))))
    return np.array(slope_angle)



def renko_DF(DF):
    "function to convert ohlc data into renko bricks"
    df = DF.copy()
    df.reset_index(inplace=True)
    df = df.iloc[:,[0,1,2,3,4,5]]
    df.columns = ["date","open","high","low","close","volume"]
    df2 = Renko(df)
    #df2.brick_size = max(0.5,round(ATR(DF,120)["ATR"][-1],0))
    df2.brick_size = max(0.5,round(ATR(DF, 120)["ATR"][-1], 0))       
    print(df2.brick_size)
    renko_df = df2.get_ohlc_data()
    renko_df["bar_num"] = np.where(renko_df["uptrend"]==True,1,np.where(renko_df["uptrend"]==False,-1,0))
    for i in range(1,len(renko_df["bar_num"])):
        if renko_df["bar_num"][i]>0 and renko_df["bar_num"][i-1]>0:
            renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
        elif renko_df["bar_num"][i]<0 and renko_df["bar_num"][i-1]<0:
            renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
    renko_df.drop_duplicates(subset="date",keep="last",inplace=True)
    return renko_df

def OBV(DF):
    """function to calculate On Balance Volume"""
    df = DF.copy()
    df['daily_ret'] = df['Close'].pct_change()
    df['direction'] = np.where(df['daily_ret']>=0,1,-1)
    df['direction'][0] = 0
    df['vol_adj'] = df['Volume'] * df['direction']
    df['obv'] = df['vol_adj'].cumsum()
    return df['obv']

def CAGR(DF):
    "function to calculate the Cumulative Annual Growth Rate of a trading strategy"
    df = DF.copy()
    df["cum_return"] = (1 + df["ret"]).cumprod()
    n = len(df)/(252*78)
    CAGR = (df["cum_return"].tolist()[-1])**(1/n) - 1
    return CAGR

def volatility(DF):
    "function to calculate annualized volatility of a trading strategy"
    df = DF.copy()
    vol = df["ret"].std() * np.sqrt(252*78)
    return vol

def sharpe(DF,rf):
    "function to calculate sharpe ratio ; rf is the risk free rate"
    df = DF.copy()
    sr = (CAGR(df) - rf)/volatility(df)
    return sr
    

def max_dd(DF):
    "function to calculate max drawdown"
    df = DF.copy()
    df["cum_return"] = (1 + df["ret"]).cumprod()
    df["cum_roll_max"] = df["cum_return"].cummax()
    df["drawdown"] = df["cum_roll_max"] - df["cum_return"]
    df["drawdown_pct"] = df["drawdown"]/df["cum_roll_max"]
    max_dd = df["drawdown_pct"].max()
    return max_dd

In [82]:
import pandas as pd
import numpy as np
import copy

def merge_ohlc_renko(historical_data):
    ohlc_renko = {}
    df = copy.deepcopy(historical_data)

    for ticker in historical_data.keys():
        print("Merging for", ticker)
        renko = renko_DF(df[ticker])
        renko.columns = ["Date", "open", "high", "low", "close", "uptrend", "bar_num"]
        df[ticker]["Date"] = df[ticker].index
        merged_data = df[ticker].merge(renko.loc[:, ["Date", "bar_num"]], how="outer", on="Date")
        merged_data["bar_num"].fillna(method='ffill', inplace=True)
        merged_data["obv"] = OBV(merged_data)
        merged_data["obv_slope"] = slope(merged_data["obv"], 5)
        ohlc_renko[ticker] = merged_data

    return ohlc_renko

def calculate_daily_returns(ohlc_renko):
    tickers_signal = {}
    tickers_ret = {}

    for ticker in ohlc_renko.keys():
        print("Calculating daily returns for", ticker)
        tickers_signal[ticker] = ""
        tickers_ret[ticker] = []

        for i in range(len(ohlc_renko[ticker])):
            if tickers_signal[ticker] == "":
                tickers_ret[ticker].append(0)
                if ohlc_renko[ticker]["bar_num"][i] >= 2 and ohlc_renko[ticker]["obv_slope"][i] > 30:
                    tickers_signal[ticker] = "Buy"
                elif ohlc_renko[ticker]["bar_num"][i] <= -2 and ohlc_renko[ticker]["obv_slope"][i] < -30:
                    tickers_signal[ticker] = "Sell"

            elif tickers_signal[ticker] == "Buy":
                tickers_ret[ticker].append((ohlc_renko[ticker]["Close"][i] / ohlc_renko[ticker]["Close"][i - 1]) - 1)
                if ohlc_renko[ticker]["bar_num"][i] <= -2 and ohlc_renko[ticker]["obv_slope"][i] < -30:
                    tickers_signal[ticker] = "Sell"
                elif ohlc_renko[ticker]["bar_num"][i] < 2:
                    tickers_signal[ticker] = ""

            elif tickers_signal[ticker] == "Sell":
                tickers_ret[ticker].append((ohlc_renko[ticker]["Close"][i - 1] / ohlc_renko[ticker]["Close"][i]) - 1)
                if ohlc_renko[ticker]["bar_num"][i] >= 2 and ohlc_renko[ticker]["obv_slope"][i] > 30:
                    tickers_signal[ticker] = "Buy"
                elif ohlc_renko[ticker]["bar_num"][i] > -2:
                    tickers_signal[ticker] = ""

        ohlc_renko[ticker]["ret"] = np.array(tickers_ret[ticker])

    return ohlc_renko

# Example usage
# historical_data = process_data(tickers, start_date, end_date)
# merged_data = merge_ohlc_renko(historical_data, tickers)
# final_data = calculate_daily_returns(merged_data, tickers)


In [84]:
final_data = calculate_daily_returns(merged_data)

Calculating daily returns for ADANIENT.NS
Calculating daily returns for ADANIPORTS.NS
Calculating daily returns for HDFCBANK.NS
Calculating daily returns for ATGL.NS
Calculating daily returns for ICICIBANK.NS
Calculating daily returns for ADANIENSOL.NS
Calculating daily returns for IRCON.NS
Calculating daily returns for ADANIGREEN.NS
Calculating daily returns for RPOWER.NS
Calculating daily returns for RELIANCE.NS
Calculating daily returns for ITC.NS
Calculating daily returns for INFY.NS
Calculating daily returns for AXISBANK.NS
Calculating daily returns for NBCC.NS
Calculating daily returns for BHEL.NS
Calculating daily returns for SPARC.NS
Calculating daily returns for IRFC.NS
Calculating daily returns for ENGINERSIN.NS
Calculating daily returns for IDEA.NS
Calculating daily returns for SBIN.NS
Calculating daily returns for CANBK.NS
Calculating daily returns for YESBANK.NS
Calculating daily returns for BAJAJ-AUTO.NS
Calculating daily returns for RVNL.NS
Calculating daily returns for 

In [89]:
merged_data = merge_ohlc_renko(historical_data)
final_data = calculate_daily_returns(merged_data)
kpi_df_OBV = calculate_kpis(final_data)

# MACD

In [98]:
def MACD(DF,a,b,c):
    """function to calculate MACD
       typical values a = 12; b =26, c =9"""
    df = DF.copy()
    df["MA_Fast"]=df["Close"].ewm(span=a,min_periods=a).mean()
    df["MA_Slow"]=df["Close"].ewm(span=b,min_periods=b).mean()
    df["MACD"]=df["MA_Fast"]-df["MA_Slow"]
    df["Signal"]=df["MACD"].ewm(span=c,min_periods=c).mean()
    df.dropna(inplace=True)
    return (df["MACD"],df["Signal"])

In [99]:
import pandas as pd
import numpy as np
import copy

def merge_ohlc_renko_with_macd(historical_data):
    ohlc_renko = {}
    df = copy.deepcopy(historical_data)

    for ticker in historical_data.keys():
        print("Merging for", ticker)
        renko = renko_DF(df[ticker])
        renko.columns = ["Date", "open", "high", "low", "close", "uptrend", "bar_num"]
        df[ticker]["Date"] = df[ticker].index
        merged_data = df[ticker].merge(renko.loc[:, ["Date", "bar_num"]], how="outer", on="Date")
        merged_data["bar_num"].fillna(method='ffill', inplace=True)
        merged_data["macd"], merged_data["macd_sig"] = MACD(merged_data, 12, 26, 9)
        merged_data["macd_slope"] = slope(merged_data["macd"], 5)
        merged_data["macd_sig_slope"] = slope(merged_data["macd_sig"], 5)
        ohlc_renko[ticker] = merged_data

    return ohlc_renko

def calculate_daily_returns_with_macd(ohlc_renko):
    tickers_signal = {}
    tickers_ret = {}

    for ticker in ohlc_renko.keys():
        print("Calculating daily returns for", ticker)
        tickers_signal[ticker] = ""
        tickers_ret[ticker] = []

        for i in range(len(ohlc_renko[ticker])):
            if tickers_signal[ticker] == "":
                tickers_ret[ticker].append(0)
                if i > 0:
                    if ohlc_renko[ticker]["bar_num"][i] >= 2 and ohlc_renko[ticker]["macd"][i] > ohlc_renko[ticker]["macd_sig"][i] and ohlc_renko[ticker]["macd_slope"][i] > ohlc_renko[ticker]["macd_sig_slope"][i]:
                        tickers_signal[ticker] = "Buy"
                    elif ohlc_renko[ticker]["bar_num"][i] <= -2 and ohlc_renko[ticker]["macd"][i] < ohlc_renko[ticker]["macd_sig"][i] and ohlc_renko[ticker]["macd_slope"][i] < ohlc_renko[ticker]["macd_sig_slope"][i]:
                        tickers_signal[ticker] = "Sell"

            elif tickers_signal[ticker] == "Buy":
                tickers_ret[ticker].append((ohlc_renko[ticker]["Close"][i] / ohlc_renko[ticker]["Close"][i - 1]) - 1)
                if i > 0:
                    if ohlc_renko[ticker]["bar_num"][i] <= -2 and ohlc_renko[ticker]["macd"][i] < ohlc_renko[ticker]["macd_sig"][i] and ohlc_renko[ticker]["macd_slope"][i] < ohlc_renko[ticker]["macd_sig_slope"][i]:
                        tickers_signal[ticker] = "Sell"
                    elif ohlc_renko[ticker]["macd"][i] < ohlc_renko[ticker]["macd_sig"][i] and ohlc_renko[ticker]["macd_slope"][i] < ohlc_renko[ticker]["macd_sig_slope"][i]:
                        tickers_signal[ticker] = ""

            elif tickers_signal[ticker] == "Sell":
                tickers_ret[ticker].append((ohlc_renko[ticker]["Close"][i - 1] / ohlc_renko[ticker]["Close"][i]) - 1)
                if i > 0:
                    if ohlc_renko[ticker]["bar_num"][i] >= 2 and ohlc_renko[ticker]["macd"][i] > ohlc_renko[ticker]["macd_sig"][i] and ohlc_renko[ticker]["macd_slope"][i] > ohlc_renko[ticker]["macd_sig_slope"][i]:
                        tickers_signal[ticker] = "Buy"
                    elif ohlc_renko[ticker]["macd"][i] > ohlc_renko[ticker]["macd_sig"][i] and ohlc_renko[ticker]["macd_slope"][i] > ohlc_renko[ticker]["macd_sig_slope"][i]:
                        tickers_signal[ticker] = ""

        ohlc_renko[ticker]["ret"] = np.array(tickers_ret[ticker])

    return ohlc_renko

# Example usage
# historical_data = process_data(tickers, start_date, end_date)
# merged_data = merge_ohlc_renko_with_macd(historical_data, tickers)
# final_data = calculate_daily_returns_with_macd(merged_data, tickers)


In [104]:
merged_data = merge_ohlc_renko_with_macd(historical_data)
final_data = calculate_daily_returns_with_macd(merged_data)
kpi_df_MACD = calculate_kpis(final_data)

Merging for ADANIENT.NS
8.0


/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]


Merging for ADANIPORTS.NS
4.0


/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]


Merging for HDFCBANK.NS
2.0


...

Merging for LT.NS
6.0


/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]


Merging for NTPC.NS
1.0


/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]


Calculating daily returns for ADANIENT.NS
Calculating daily returns for ADANIPORTS.NS
Calculating daily returns for HDFCBANK.NS
Calculating daily returns for ATGL.NS
Calculating daily returns for ICICIBANK.NS
Calculating daily returns for ADANIENSOL.NS
Calculating daily returns for IRCON.NS
Calculating daily returns for ADANIGREEN.NS
Calculating daily returns for RPOWER.NS
Calculating daily returns for RELIANCE.NS
Calculating daily returns for ITC.NS
Calculating daily returns for INFY.NS
Calculating daily returns for AXISBANK.NS
Calculating daily returns for NBCC.NS
Calculating daily returns for BHEL.NS
Calculating daily returns for SPARC.NS
Calculating daily returns for IRFC.NS
Calculating daily returns for ENGINERSIN.NS
Calculating daily returns for IDEA.NS
Calculating daily returns for SBIN.NS
Calculating daily returns for CANBK.NS
Calculating daily returns for YESBANK.NS
Calculating daily returns for BAJAJ-AUTO.NS
Calculating daily returns for RVNL.NS
Calculating daily returns for 

In [105]:
kpi_df_MACD

CAGR  Sharpe Ratio  Max Drawdown  Actual Return
ADANIENT.NS     0.866949      2.595737      0.075118       1.050629
ADANIPORTS.NS   1.349708      4.548719      0.054242       1.069920
HDFCBANK.NS    -0.225770     -2.460600      0.039279       0.979960
ATGL.NS        -0.504391     -0.747180      0.126241       0.945981
ICICIBANK.NS   -0.042735     -0.557057      0.022865       0.996551
ADANIENSOL.NS  33.017324     56.508238      0.072143       1.321825
IRCON.NS       -0.802876     -2.897724      0.132884       0.879440
ADANIGREEN.NS   1.846978      3.428957      0.095637       1.086292
RPOWER.NS       6.504363     15.238040      0.114383       1.172861
RELIANCE.NS     0.455744      3.262037      0.026817       1.030153
ITC.NS         -0.302347     -2.782691      0.042152       0.971919
INFY.NS         0.578323      2.868984      0.057473       1.036763
AXISBANK.NS    -0.057925     -0.526425      0.059818       0.995291
NBCC.NS         1.176957      3.499148      0.062232       1.063476
BHEL.NS        -0.821755     -2.426878      0.174989       0.872464
SPARC.NS       16.110393     32.170016      0.069984       1.251884
IRFC.NS        -0.597240     -1.395163      0.140378       0.930583
ENGINERSIN.NS   0.860437      2.080747      0.086187       1.050339
IDEA.NS         6.384045     14.252565      0.091548       1.171363
SBIN.NS         0.292812      1.331226      0.036938       1.020525
CANBK.NS        0.385807      1.586599      0.042860       1.026149
YESBANK.NS     -0.647649     -2.165728      0.100072       0.920791
BAJAJ-AUTO.NS  -0.083153     -0.550861      0.049563       0.993156
RVNL.NS        -0.914917     -2.692602      0.188366       0.822885
BANDHANBNK.NS   2.124820      8.691281      0.029492       1.094324
BIOCON.NS       0.986079      4.095221      0.036944       1.055783
NATIONALUM.NS   7.725657     17.960844      0.066155       1.186936
AMBUJACEM.NS    0.017070     -0.030444      0.069805       1.001340
AWL.NS          0.395670      1.019373      0.109913       1.026724
PNB.NS         -0.050787     -0.346222      0.061277       0.995885
KOTAKBANK.NS    0.493300      3.573857      0.028612       1.032231
TATAMOTORS.NS   0.619463      3.014137      0.041530       1.038875
TCS.NS          0.979019      5.365533      0.034952       1.055486
IRCTC.NS        3.794220      9.928186      0.094097       1.132015
TATASTEEL.NS    1.082467      7.066391      0.026735       1.059749
HAL.NS          1.326380      5.532679      0.039198       1.069075
ALOKINDS.NS     4.377856      9.195696      0.087406       1.142350
VEDL.NS         0.352982      1.797619      0.033041       1.024204
RAILTEL.NS     -0.976306     -1.891707      0.297312       0.743731
PAYTM.NS       -0.446097     -1.509376      0.120617       0.954339
HINDPETRO.NS   -0.266479     -0.856052      0.105703       0.975782
MARUTI.NS      -0.148719     -1.142730      0.036065       0.987343
PFC.NS          1.925560      5.453607      0.049090       1.088635
ZOMATO.NS       1.141978      3.857616      0.087577       1.062114
COALINDIA.NS    2.121882      8.681946      0.044724       1.094243
BANKBARODA.NS   0.480617      2.255231      0.051442       1.031535
RECLTD.NS       5.364650     14.361368      0.047017       1.157676
WIPRO.NS        2.167989      8.478078      0.040161       1.095513
LT.NS           0.200898      1.172540      0.049549       1.014588
NTPC.NS         0.046135      0.085844      0.058125       1.003574

# Combined logic

In [149]:
import copy

def merge_ohlc_renko_with_indicators(historical_data):
    ohlc_renko = {}
    df = copy.deepcopy(historical_data)

    for ticker in historical_data.keys():
        print("Merging for", ticker)
        # Generate Renko data
        renko = renko_DF(df[ticker])
        renko.columns = ["Date", "open", "high", "low", "close", "uptrend", "bar_num"]

        # Merge Renko data with OHLC data
        df[ticker]["Date"] = df[ticker].index
        merged_data = df[ticker].merge(renko.loc[:, ["Date", "bar_num"]], how="outer", on="Date")
        merged_data["bar_num"].fillna(method='ffill', inplace=True)

        # Calculate MACD indicators
        merged_data["macd"], merged_data["macd_sig"] = MACD(merged_data, 12, 26, 9)
        merged_data["macd_slope"] = slope(merged_data["macd"], 5)
        merged_data["macd_sig_slope"] = slope(merged_data["macd_sig"], 5)

        # Calculate OBV and its slope
        merged_data["obv"] = OBV(merged_data)
        merged_data["obv_slope"] = slope(merged_data["obv"], 5)

        ohlc_renko[ticker] = merged_data

    return ohlc_renko


In [150]:
import numpy as np

def calculate_daily_returns_combined(ohlc_renko):
    tickers_signal = {}
    tickers_ret = {}

    for ticker in ohlc_renko.keys():
        print("Calculating daily returns for", ticker)
        tickers_signal[ticker] = ""
        tickers_ret[ticker] = []

        for i in range(len(ohlc_renko[ticker])):
            if tickers_signal[ticker] == "":
                tickers_ret[ticker].append(0)
                if i > 0:
                    # Combined conditions for OBV and MACD
                    if ohlc_renko[ticker]["bar_num"][i] >= 2 and ((ohlc_renko[ticker]["obv_slope"][i] > 30) or (ohlc_renko[ticker]["macd"][i] > ohlc_renko[ticker]["macd_sig"][i] and ohlc_renko[ticker]["macd_slope"][i] > ohlc_renko[ticker]["macd_sig_slope"][i])):
                        tickers_signal[ticker] = "Buy"
                    elif ohlc_renko[ticker]["bar_num"][i] <= -2 and ((ohlc_renko[ticker]["obv_slope"][i] < -30) or (ohlc_renko[ticker]["macd"][i] < ohlc_renko[ticker]["macd_sig"][i] and ohlc_renko[ticker]["macd_slope"][i] < ohlc_renko[ticker]["macd_sig_slope"][i])):
                        tickers_signal[ticker] = "Sell"

            elif tickers_signal[ticker] == "Buy":
                tickers_ret[ticker].append((ohlc_renko[ticker]["Close"][i] / ohlc_renko[ticker]["Close"][i - 1]) - 1)
                if i > 0:
                    # Combined conditions for exiting Buy position
                    if ohlc_renko[ticker]["bar_num"][i] <= -2 and ((ohlc_renko[ticker]["obv_slope"][i] < -30) or (ohlc_renko[ticker]["macd"][i] < ohlc_renko[ticker]["macd_sig"][i] and ohlc_renko[ticker]["macd_slope"][i] < ohlc_renko[ticker]["macd_sig_slope"][i])):
                        tickers_signal[ticker] = "Sell"
                    elif ohlc_renko[ticker]["macd"][i] < ohlc_renko[ticker]["macd_sig"][i] and ohlc_renko[ticker]["macd_slope"][i] < ohlc_renko[ticker]["macd_sig_slope"][i]:
                        tickers_signal[ticker] = ""

            elif tickers_signal[ticker] == "Sell":
                tickers_ret[ticker].append((ohlc_renko[ticker]["Close"][i - 1] / ohlc_renko[ticker]["Close"][i]) - 1)
                if i > 0:
                    # Combined conditions for exiting Sell position
                    if ohlc_renko[ticker]["bar_num"][i] >= 2 and ((ohlc_renko[ticker]["obv_slope"][i] > 30) or (ohlc_renko[ticker]["macd"][i] > ohlc_renko[ticker]["macd_sig"][i] and ohlc_renko[ticker]["macd_slope"][i] > ohlc_renko[ticker]["macd_sig_slope"][i])):
                        tickers_signal[ticker] = "Buy"
                    elif ohlc_renko[ticker]["macd"][i] > ohlc_renko[ticker]["macd_sig"][i] and ohlc_renko[ticker]["macd_slope"][i] > ohlc_renko[ticker]["macd_sig_slope"][i]:
                        tickers_signal[ticker] = ""

        ohlc_renko[ticker]["ret"] = np.array(tickers_ret[ticker])

    return ohlc_renko


In [151]:
merged_data = merge_ohlc_renko_with_indicators(historical_data)
final_data = calculate_daily_returns_combined(merged_data)
kpi_df_combines = calculate_kpis(final_data)

Merging for ADANIENT.NS
0.5
Merging for ADANIPORTS.NS
0.5
Merging for HDFCBANK.NS
0.5


/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:63: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/inde

Merging for ATGL.NS
0.5
Merging for ICICIBANK.NS
0.5
Merging for ADANIENSOL.NS
0.5
Merging for IRCON.NS
0.5


/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:63: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/inde

Merging for ADANIGREEN.NS
0.5
Merging for RPOWER.NS
0.5
Merging for RELIANCE.NS
0.5
Merging for ITC.NS
0.5


...

/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:63: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['direction'][0] = 0
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view

Merging for RECLTD.NS
0.5
Merging for WIPRO.NS
0.5
Merging for LT.NS
0.5
Merging for NTPC.NS
0.5


/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:63: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['direction'][0] = 0
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view

Calculating daily returns for ADANIENT.NS
Calculating daily returns for ADANIPORTS.NS
Calculating daily returns for HDFCBANK.NS
Calculating daily returns for ATGL.NS
Calculating daily returns for ICICIBANK.NS
Calculating daily returns for ADANIENSOL.NS
Calculating daily returns for IRCON.NS
Calculating daily returns for ADANIGREEN.NS
Calculating daily returns for RPOWER.NS
Calculating daily returns for RELIANCE.NS
Calculating daily returns for ITC.NS
Calculating daily returns for INFY.NS
Calculating daily returns for AXISBANK.NS
Calculating daily returns for NBCC.NS
Calculating daily returns for BHEL.NS
Calculating daily returns for SPARC.NS
Calculating daily returns for IRFC.NS
Calculating daily returns for ENGINERSIN.NS
Calculating daily returns for IDEA.NS
Calculating daily returns for SBIN.NS
Calculating daily returns for CANBK.NS
Calculating daily returns for YESBANK.NS
Calculating daily returns for BAJAJ-AUTO.NS
Calculating daily returns for RVNL.NS
Calculating daily returns for 

/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)


In [152]:
kpi_df_combines

CAGR  Sharpe Ratio  Max Drawdown  Actual Return
ADANIENT.NS   -7.381916e-01 -4.223897e+00      0.010963       0.996257
ADANIPORTS.NS  1.932474e+01  1.043088e+02      0.008952       1.008463
HDFCBANK.NS    2.179393e+01  2.474588e+02      0.003707       1.008787
ATGL.NS       -8.182437e-01 -4.845961e+00      0.008419       0.995240
ICICIBANK.NS   3.956540e+00  2.380228e+01      0.004894       1.004489
ADANIENSOL.NS -7.031695e-01 -3.285013e+00      0.006644       0.996607
IRCON.NS      -2.567036e-01 -1.467133e+00      0.009545       0.999170
ADANIGREEN.NS  2.235368e+00  1.281437e+01      0.007829       1.003291
RPOWER.NS     -9.999870e-01 -2.848263e+00      0.030981       0.969019
RELIANCE.NS    5.695693e-02  2.974873e-01      0.003560       1.000155
ITC.NS         7.884745e+00  6.469321e+01      0.002725       1.006131
INFY.NS       -6.810938e-01 -3.731552e+00      0.008462       0.996807
AXISBANK.NS    1.205241e+01  7.961103e+01      0.006134       1.007214
NBCC.NS        0.000000e+00          -inf      0.000000       1.000000
BHEL.NS       -9.864021e-01 -4.683379e+00      0.016225       0.988046
SPARC.NS       7.870281e+03  1.108988e+04      0.022632       1.025420
IRFC.NS        0.000000e+00          -inf      0.000000       1.000000
ENGINERSIN.NS  6.424735e+02  1.946308e+03      0.011625       1.018260
IDEA.NS       -9.841347e-01 -2.277071e+00      0.022988       0.988473
SBIN.NS        1.545482e+01  1.166865e+02      0.004753       1.007867
CANBK.NS       8.720210e-01  4.881554e+00      0.006630       1.001756
YESBANK.NS     9.449036e-03 -4.316880e-02      0.020585       1.000026
BAJAJ-AUTO.NS  3.029274e+00  2.207419e+01      0.003371       1.003907
RVNL.NS       -9.632204e-01 -8.531035e+00      0.009735       0.990801
BANDHANBNK.NS  3.392537e+03  8.985976e+03      0.009755       1.023008
BIOCON.NS      1.327675e+06  2.886471e+06      0.011588       1.040239
NATIONALUM.NS  3.204638e-01  1.831731e+00      0.005063       1.000778
AMBUJACEM.NS   3.494864e+03  1.394073e+04      0.006100       1.023093
AWL.NS        -1.333610e-01 -1.006376e+00      0.008706       0.999600
PNB.NS         0.000000e+00          -inf      0.000000       1.000000
KOTAKBANK.NS   3.139062e-01  3.546995e+00      0.003984       1.000764
TATAMOTORS.NS -5.101084e-01 -3.985921e+00      0.007391       0.998005
TCS.NS        -8.394936e-01 -7.464756e+00      0.006722       0.994894
IRCTC.NS       1.414081e+01  6.741966e+01      0.007260       1.007633
TATASTEEL.NS   0.000000e+00          -inf      0.000000       1.000000
HAL.NS         1.212350e+01  5.048721e+01      0.009978       1.007230
ALOKINDS.NS    1.584974e+03  1.960023e+03      0.024653       1.020833
VEDL.NS       -7.885227e-01 -4.639382e+00      0.011428       0.995662
RAILTEL.NS     1.882014e+01  7.228896e+01      0.010128       1.008392
PAYTM.NS       4.407535e+02  2.330153e+03      0.003199       1.017189
HINDPETRO.NS   1.168160e+03  5.713997e+03      0.005238       1.019963
MARUTI.NS     -1.873250e-01 -2.225540e+00      0.004246       0.999420
PFC.NS         4.262903e+01  1.948129e+02      0.004860       1.010621
ZOMATO.NS      6.689838e+01  3.035005e+02      0.006447       1.011872
COALINDIA.NS   2.047760e+00  1.489163e+01      0.005542       1.003123
BANKBARODA.NS  4.813286e-01  1.818371e+00      0.010129       1.001100
RECLTD.NS      2.979724e+01  1.579699e+02      0.005947       1.009637
WIPRO.NS      -2.651989e-01 -2.199908e+00      0.003941       0.999138
LT.NS         -9.099855e-01 -4.659343e+00      0.019112       0.993285
NTPC.NS        8.659413e-01  4.964622e+00      0.005871       1.001747

# testing

In [121]:
## Downloading Data
### Selecting the stocks traded in terms of value
bhav=pd.read_csv("/Users/alekhsaxena/Downloads/cm03JAN2024bhav.csv")
bhav=bhav.sort_values(by='TOTTRDVAL',ascending=False)
bhav=bhav[0:50]
bhav['ticker']=bhav['SYMBOL']+'.NS'
tickers = bhav['ticker']
tickers

start_date = (dt.datetime.today() - dt.timedelta(1)).date()
end_date = dt.datetime.today().date()
historical_data = download_intraday_data(tickers, start_date, end_date, interval='5m')

for ticker in historical_data.keys():
    historical_data[ticker]=historical_data[ticker].drop('Close',axis=1)
    historical_data[ticker].columns=['Open', 'High', 'Low', 'Close', 'Volume']

[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%*******

In [122]:
processed_data=process_data(historical_data)
kpi_df_breakout = calculate_kpis(processed_data)

merged_data = merge_ohlc_renko(historical_data)
final_data = calculate_daily_returns(merged_data)
kpi_df_OBV = calculate_kpis(final_data)


merged_data = merge_ohlc_renko_with_macd(historical_data)
final_data = calculate_daily_returns_with_macd(merged_data)
kpi_df_MACD = calculate_kpis(final_data)

merged_data = merge_ohlc_renko_with_indicators(historical_data)
final_data = calculate_daily_returns_combined(merged_data)
kpi_df_combines = calculate_kpis(final_data)

Calculating KPIs for ADANIENT.NS
Calculating KPIs for ADANIPORTS.NS
Calculating KPIs for HDFCBANK.NS
Calculating KPIs for ATGL.NS
Calculating KPIs for ICICIBANK.NS
Calculating KPIs for ADANIENSOL.NS
Calculating KPIs for IRCON.NS
Calculating KPIs for ADANIGREEN.NS
Calculating KPIs for RPOWER.NS
Calculating KPIs for RELIANCE.NS
Calculating KPIs for ITC.NS
Calculating KPIs for INFY.NS
Calculating KPIs for AXISBANK.NS
Calculating KPIs for NBCC.NS
Calculating KPIs for BHEL.NS
Calculating KPIs for SPARC.NS
Calculating KPIs for IRFC.NS
Calculating KPIs for ENGINERSIN.NS
Calculating KPIs for IDEA.NS
Calculating KPIs for SBIN.NS
Calculating KPIs for CANBK.NS
Calculating KPIs for YESBANK.NS
Calculating KPIs for BAJAJ-AUTO.NS
Calculating KPIs for RVNL.NS
Calculating KPIs for BANDHANBNK.NS
Calculating KPIs for BIOCON.NS
Calculating KPIs for NATIONALUM.NS
Calculating KPIs for AMBUJACEM.NS
Calculating KPIs for AWL.NS
Calculating KPIs for PNB.NS
Calculating KPIs for KOTAKBANK.NS
Calculating KPIs for 

/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarnin

Merging for ATGL.NS
0.5
Merging for ICICIBANK.NS
0.5
Merging for ADANIENSOL.NS
0.5
Merging for IRCON.NS
0.5
Merging for ADANIGREEN.NS
0.5
Merging for RPOWER.NS
0.5


/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:63: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/inde

Merging for RELIANCE.NS
0.5
Merging for ITC.NS
0.5
Merging for INFY.NS
0.5
Merging for AXISBANK.NS
0.5
Merging for NBCC.NS
0.5
Merging for BHEL.NS
0.5
Merging for SPARC.NS
0.5
Merging for IRFC.NS
0.5


...

/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/inde

Merging for COALINDIA.NS
0.5
Merging for BANKBARODA.NS
0.5
Merging for RECLTD.NS
0.5
Merging for WIPRO.NS
0.5
Merging for LT.NS
0.5


/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/inde

Merging for NTPC.NS
0.5
Calculating daily returns for ADANIENT.NS
Calculating daily returns for ADANIPORTS.NS
Calculating daily returns for HDFCBANK.NS
Calculating daily returns for ATGL.NS
Calculating daily returns for ICICIBANK.NS
Calculating daily returns for ADANIENSOL.NS
Calculating daily returns for IRCON.NS
Calculating daily returns for ADANIGREEN.NS
Calculating daily returns for RPOWER.NS
Calculating daily returns for RELIANCE.NS
Calculating daily returns for ITC.NS
Calculating daily returns for INFY.NS
Calculating daily returns for AXISBANK.NS
Calculating daily returns for NBCC.NS
Calculating daily returns for BHEL.NS
Calculating daily returns for SPARC.NS
Calculating daily returns for IRFC.NS
Calculating daily returns for ENGINERSIN.NS
Calculating daily returns for IDEA.NS
Calculating daily returns for SBIN.NS
Calculating daily returns for CANBK.NS
Calculating daily returns for YESBANK.NS
Calculating daily returns for BAJAJ-AUTO.NS
Calculating daily returns for RVNL.NS
Calcul

/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarnin

In [153]:
def merge_kpi_dataframes(kpi_df_breakout, kpi_df_OBV, kpi_df_MACD, kpi_df_combines):
    # Merge the DataFrames on their indices (tickers)
    merged_df = kpi_df_breakout.join(kpi_df_OBV, lsuffix='_breakout', rsuffix='_OBV')
    merged_df = merged_df.join(kpi_df_MACD, rsuffix='_MACD')
    merged_df = merged_df.join(kpi_df_combines, rsuffix='_combined')

    # Optionally, rename columns to avoid any duplicate column names
    # Example: merged_df.rename(columns={'Return': 'Return_breakout', ...}, inplace=True)

    return merged_df

# Example usage
# processed_data = process_data(historical_data)
# kpi_df_breakout = calculate_kpis(processed_data)

# merged_data = merge_ohlc_renko(historical_data)


In [155]:
merged_kpi_df=merge_kpi_dataframes(kpi_df_breakout, kpi_df_OBV, kpi_df_MACD, kpi_df_combines)

In [130]:
## Downloading Data
### Selecting the stocks traded in terms of value
bhav=pd.read_csv("/Users/alekhsaxena/Downloads/cm03JAN2024bhav.csv")
bhav=bhav.sort_values(by='TOTTRDVAL',ascending=False)
bhav=bhav[0:50]
bhav['ticker']=bhav['SYMBOL']+'.NS'
tickers = bhav['ticker']
tickers

date_to_check = datetime.date(2023, 1, 3)  # Replace with the date you want to check
was_trading_day = is_trading_day(date_to_check)

if was_trading_day:
    start_date = (dt.datetime.today() - dt.timedelta(1)).date()
    end_date = dt.datetime.today().date()
    historical_data = download_intraday_data(tickers, start_date, end_date, interval='5m')

    for ticker in historical_data.keys():
        historical_data[ticker]=historical_data[ticker].drop('Close',axis=1)
        historical_data[ticker].columns=['Open', 'High', 'Low', 'Close', 'Volume']


    processed_data=process_data(historical_data)
    kpi_df_breakout = calculate_kpis(processed_data)

    merged_data = merge_ohlc_renko(historical_data)
    final_data = calculate_daily_returns(merged_data)
    kpi_df_OBV = calculate_kpis(final_data)


    merged_data = merge_ohlc_renko_with_macd(historical_data)
    final_data = calculate_daily_returns_with_macd(merged_data)
    kpi_df_MACD = calculate_kpis(final_data)
    
    merged_data = merge_ohlc_renko_with_indicators(historical_data)
    final_data = calculate_daily_returns_combined(merged_data)
    kpi_df_combines = calculate_kpis(final_data)
    
    

    merged_kpi_df=merge_kpi_dataframes(kpi_df_breakout, kpi_df_OBV, kpi_df_MACD, kpi_df_combines)
    merged_kpi_df['Start Date'] = start_date
    
else:
    
print('Not a trading day!')

[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%*******

/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarnin

Merging for ICICIBANK.NS
0.5
Merging for ADANIENSOL.NS
0.5
Merging for IRCON.NS
0.5
Merging for ADANIGREEN.NS
0.5
Merging for RPOWER.NS
0.5
Merging for RELIANCE.NS
0.5
Merging for ITC.NS
0.5


/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:63: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/inde

Merging for INFY.NS
0.5
Merging for AXISBANK.NS
0.5
Merging for NBCC.NS
0.5
Merging for BHEL.NS
0.5
Merging for SPARC.NS
0.5
Merging for IRFC.NS
0.5
Merging for ENGINERSIN.NS
0.5


...

/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/inde

Merging for PAYTM.NS
0.5
Merging for HINDPETRO.NS
0.5
Merging for MARUTI.NS
0.5
Merging for PFC.NS
0.5
Merging for ZOMATO.NS
0.5


/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/inde

Merging for COALINDIA.NS
0.5
Merging for BANKBARODA.NS
0.5
Merging for RECLTD.NS
0.5
Merging for WIPRO.NS
0.5
Merging for LT.NS
0.5
Merging for NTPC.NS
0.5
Calculating daily returns for ADANIENT.NS
Calculating daily returns for ADANIPORTS.NS
Calculating daily returns for HDFCBANK.NS
Calculating daily returns for ATGL.NS
Calculating daily returns for ICICIBANK.NS
Calculating daily returns for ADANIENSOL.NS
Calculating daily returns for IRCON.NS
Calculating daily returns for ADANIGREEN.NS
Calculating daily returns for RPOWER.NS
Calculating daily returns for RELIANCE.NS
Calculating daily returns for ITC.NS
Calculating daily returns for INFY.NS
Calculating daily returns for AXISBANK.NS
Calculating daily returns for NBCC.NS
Calculating daily returns for BHEL.NS
Calculating daily returns for SPARC.NS
Calculating daily returns for IRFC.NS
Calculating daily returns for ENGINERSIN.NS
Calculating daily returns for IDEA.NS
Calculating daily returns for SBIN.NS
Calculating daily returns for CANBK.

/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/inde

In [208]:
dt.date(2024, 1, 6)-dt.timedelta(days=60)

datetime.date(2023, 11, 7)

In [210]:
import pandas as pd
import datetime as dt

# Assuming all necessary functions are defined/imported here
# ...

# Read the bhav file
bhav = pd.read_csv("/Users/alekhsaxena/Downloads/cm03JAN2024bhav.csv")
bhav = bhav.sort_values(by='TOTTRDVAL', ascending=False)
bhav = bhav[0:50]
bhav['ticker'] = bhav['SYMBOL'] + '.NS'
tickers = bhav['ticker'].tolist()

# Initialize an empty DataFrame for the final results
final_results = pd.DataFrame()

# Loop through the date range
start_loop_date = dt.date(2023, 11, 8)
end_loop_date = dt.date(2024, 1, 6)
current_date = start_loop_date

print(current_date)
while current_date <= end_loop_date:
    if is_trading_day(current_date):
        start_date = current_date
        end_date = current_date + dt.timedelta(days=1)

        historical_data = download_intraday_data(tickers, start_date, end_date, interval='5m')

        for ticker in historical_data.keys():
            historical_data[ticker]=historical_data[ticker].drop('Close',axis=1)
            historical_data[ticker].columns=['Open', 'High', 'Low', 'Close', 'Volume']


        processed_data=process_data(historical_data)
        kpi_df_breakout = calculate_kpis(processed_data)

        merged_data = merge_ohlc_renko(historical_data)
        final_data = calculate_daily_returns(merged_data)
        kpi_df_OBV = calculate_kpis(final_data)


        merged_data = merge_ohlc_renko_with_macd(historical_data)
        final_data = calculate_daily_returns_with_macd(merged_data)
        kpi_df_MACD = calculate_kpis(final_data)

        merged_data = merge_ohlc_renko_with_indicators(historical_data)
        final_data = calculate_daily_returns_combined(merged_data)
        kpi_df_combines = calculate_kpis(final_data)
        # ...

        # Merge KPI dataframes
        merged_kpi_df = merge_kpi_dataframes(kpi_df_breakout, kpi_df_OBV, kpi_df_MACD, kpi_df_combines)
        merged_kpi_df=merged_kpi_df.reset_index()
        merged_kpi_df['Start Date'] = start_date

        # Append to the final results
        final_results = final_results.append(merged_kpi_df)

    else:
        print(f'{current_date} is not a trading day!')

    # Move to the next day
    current_date += dt.timedelta(days=1)

# Display or save the final results
#print(final_results)


2023-11-08
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************1

/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarning: divide by zero encountered in double_scalars
  sr = (CAGR(df) - rf)/volatility(df)
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:85: RuntimeWarnin

Calculating KPIs for HAL.NS
Calculating KPIs for ALOKINDS.NS
Calculating KPIs for VEDL.NS
Calculating KPIs for RAILTEL.NS
Calculating KPIs for PAYTM.NS
Calculating KPIs for HINDPETRO.NS
Calculating KPIs for MARUTI.NS
Calculating KPIs for PFC.NS
Calculating KPIs for ZOMATO.NS
Calculating KPIs for COALINDIA.NS
Calculating KPIs for BANKBARODA.NS
Calculating KPIs for RECLTD.NS
Calculating KPIs for WIPRO.NS
Calculating KPIs for LT.NS
Calculating KPIs for NTPC.NS
Merging for ADANIENT.NS
0.5
Merging for ADANIPORTS.NS
0.5
Merging for HDFCBANK.NS
0.5
Merging for ATGL.NS
0.5
Merging for ICICIBANK.NS
0.5
Merging for ADANIENSOL.NS
0.5
Merging for IRCON.NS
0.5
Merging for ADANIGREEN.NS
0.5
Merging for RPOWER.NS
0.5
Merging for RELIANCE.NS
0.5
Merging for ITC.NS
0.5
Merging for INFY.NS
0.5


/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  renko_df["bar_num"][i]+=renko_df["bar_num"][i-1]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/169817028.py:63: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/inde

Merging for AXISBANK.NS
0.5
Merging for NBCC.NS
0.5
Merging for BHEL.NS
0.5
Merging for SPARC.NS
0.5
Merging for IRFC.NS
0.5
Merging for ENGINERSIN.NS
0.5
Merging for IDEA.NS
0.5
Merging for SBIN.NS
0.5
Merging for CANBK.NS
0.5


...


[*********************100%%**********************]  1 of 1 completed


1 Failed download:
['LT.NS']: Exception('%ticker%: No price data found, symbol may be delisted (5m 2024-01-06 -> 2024-01-07)')



[*********************100%%**********************]  1 of 1 completed


1 Failed download:
['NTPC.NS']: Exception('%ticker%: No price data found, symbol may be delisted (5m 2024-01-06 -> 2024-01-07)')


/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/874720328.py:58: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_results = final_results.append(merged_kpi_df)


In [212]:
data=final_results[['index','Actual Return_breakout','Actual Return_OBV','Actual Return','Actual Return_combined','Start Date']].copy()


In [213]:
data.to_csv('final_010624.csv')

In [224]:
training = data[(data['Start Date'] >= dt.date(2023, 11, 8)) & (data['Start Date'] < dt.date(2023, 12, 8))]
testing = data[(data['Start Date'] >= dt.date(2023, 12, 8)) & (data['Start Date'] < dt.date(2024, 1, 6))]

In [225]:
# Calculating the proportion of days with return > 1 for each stock and each return metric

training = data[(data['Start Date'] >= dt.date(2023, 11, 8)) & (data['Start Date'] < dt.date(2023, 12, 8))]
testing = data[(data['Start Date'] >= dt.date(2023, 12, 8)) & (data['Start Date'] < dt.date(2024, 1, 6))]

def calculate_proportion_above_one(data, return_column):
    return data.groupby('index')[return_column].apply(lambda x: (x > 1).mean())

# Applying the function for each return metric
proportion_breakout = calculate_proportion_above_one(training, 'Actual Return_breakout')
proportion_obv = calculate_proportion_above_one(training, 'Actual Return_OBV')
proportion_actual_return = calculate_proportion_above_one(training, 'Actual Return')
proportion_combined = calculate_proportion_above_one(training, 'Actual Return_combined')

# Combining the results
proportions = pd.DataFrame({
    'Proportion >1 Return_breakout': proportion_breakout,
    'Proportion >1 Return_OBV': proportion_obv,
    'Proportion >1 Actual Return': proportion_actual_return,
    'Proportion >1 Return_combined': proportion_combined
})

# Sorting the results to find the top stocks for each metric
top_proportion_breakout = proportions.sort_values('Proportion >1 Return_breakout', ascending=False)
top_proportion_obv = proportions.sort_values('Proportion >1 Return_OBV', ascending=False)
top_proportion_actual_return = proportions.sort_values('Proportion >1 Actual Return', ascending=False)
top_proportion_combined = proportions.sort_values('Proportion >1 Return_combined', ascending=False)

# Displaying the top stocks for each return metric
top_stocks_by_proportion = {
    'Top Stocks by Proportion >1 Return_breakout': top_proportion_breakout.head(),
    'Top Stocks by Proportion >1 Return_OBV': top_proportion_obv.head(),
    'Top Stocks by Proportion >1 Actual Return': top_proportion_actual_return.head(),
    'Top Stocks by Proportion >1 Return_combined': top_proportion_combined.head()
}

#top_stocks_by_proportion


In [229]:
top_proportion_combined.head(5).index

Index(['AXISBANK.NS', 'IRCTC.NS', 'COALINDIA.NS', 'RELIANCE.NS',
       'ADANIENT.NS'],
      dtype='object', name='index')

In [232]:
testing.head()

index  Actual Return_breakout  Actual Return_OBV  Actual Return  \
0    ADANIENT.NS                1.000000           0.980231       1.009299   
1  ADANIPORTS.NS                0.994776           0.982947       1.014982   
2    HDFCBANK.NS                0.999365           0.990864       1.001090   
3        ATGL.NS                0.989120           0.967722       1.022163   
4   ICICIBANK.NS                1.001685           1.004247       1.002628   

   Actual Return_combined  Start Date  
0                0.991237  2023-12-08  
1                0.998171  2023-12-08  
2                0.990809  2023-12-08  
3                0.987381  2023-12-08  
4                1.003133  2023-12-08

In [277]:
#selected_stocks=testing[testing['index'].isin(top_proportion_combined.head(10).index)]

sorted_by_combined.head(10).index


selected_stocks=testing[testing['index'].isin(sorted_by_combined.head(16).index)]

In [278]:
testing['Actual Return_combined'].prod()

3.4579277836760265

In [279]:
selected_stocks['Actual Return_combined'].prod()

1.597077784327907

In [258]:
selected_stocks.groupby(by='index')['Actual Return_combined'].prod()

index
ADANIENT.NS     0.945919
AXISBANK.NS     0.991734
BHEL.NS         1.035819
COALINDIA.NS    0.995236
IRCTC.NS        1.145473
PFC.NS          1.006709
RECLTD.NS       1.047471
RELIANCE.NS     1.010804
TCS.NS          0.973747
WIPRO.NS        1.055151
Name: Actual Return_combined, dtype: float64

In [283]:
# Calculating the mean for each return type for each stock
start_loop_date = dt.date(2023, 11, 8)
end_loop_date = dt.date(2024, 1, 6)


training = data[(data['Start Date'] >= dt.date(2023, 11, 8)) & (data['Start Date'] < dt.date(2023, 11, 9))]
testing = data[(data['Start Date'] >= dt.date(2023, 11, 9)) & (data['Start Date'] < dt.date(2023, 11, 10))]
mean_returns = training.groupby('index').mean()[['Actual Return_breakout', 'Actual Return_OBV', 'Actual Return', 'Actual Return_combined']]

# Sorting the stocks based on each return type to find the top stocks
sorted_by_breakout = mean_returns.sort_values('Actual Return_breakout', ascending=False)
sorted_by_obv = mean_returns.sort_values('Actual Return_OBV', ascending=False)
sorted_by_actual_return = mean_returns.sort_values('Actual Return', ascending=False)
sorted_by_combined = mean_returns.sort_values('Actual Return_combined', ascending=False)

# Displaying the top stocks for each return type
top_stocks = {
    'Top Stocks by Actual Return_breakout': sorted_by_breakout.head(),
    'Top Stocks by Actual Return_OBV': sorted_by_obv.head(),
    'Top Stocks by Actual Return': sorted_by_actual_return.head(),
    'Top Stocks by Actual Return_combined': sorted_by_combined.head()
}


selected_stocks=testing[testing['index'].isin(sorted_by_combined.head(5).index)]
selected_stocks['Actual Return_combined'].prod()


/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/535587805.py:5: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  mean_returns = training.groupby('index').mean()[['Actual Return_breakout', 'Actual Return_OBV', 'Actual Return', 'Actual Return_combined']]


0.9754182824896366

In [ ]:
# Calculating the mean for each return type for each stock
start_loop_date = dt.date(2023, 11, 8)
end_loop_date = dt.date(2024, 1, 6)


training = data[(data['Start Date'] >= dt.date(2023, 11, 8)) & (data['Start Date'] < dt.date(2023, 11, 9))]
testing = data[(data['Start Date'] >= dt.date(2023, 11, 9)) & (data['Start Date'] < dt.date(2023, 11, 10))]
mean_returns = training.groupby('index').mean()[['Actual Return_breakout', 'Actual Return_OBV', 'Actual Return', 'Actual Return_combined']]

# Sorting the stocks based on each return type to find the top stocks
sorted_by_breakout = mean_returns.sort_values('Actual Return_breakout', ascending=False)
sorted_by_obv = mean_returns.sort_values('Actual Return_OBV', ascending=False)
sorted_by_actual_return = mean_returns.sort_values('Actual Return', ascending=False)
sorted_by_combined = mean_returns.sort_values('Actual Return_combined', ascending=False)

# Displaying the top stocks for each return type
top_stocks = {
    'Top Stocks by Actual Return_breakout': sorted_by_breakout.head(),
    'Top Stocks by Actual Return_OBV': sorted_by_obv.head(),
    'Top Stocks by Actual Return': sorted_by_actual_return.head(),
    'Top Stocks by Actual Return_combined': sorted_by_combined.head()
}


selected_stocks=testing[testing['index'].isin(sorted_by_combined.head(5).index)]
selected_stocks['Actual Return_combined'].prod()


In [290]:
import datetime as dt
import pandas as pd

# Assuming 'data' is your DataFrame

start_loop_date = dt.date(2023, 11, 8)
end_loop_date = dt.date(2024, 1, 6)
current_date = start_loop_date

product_of_returns = []

while current_date <= end_loop_date:
    try:
        training = data[(data['Start Date'] >= current_date) & (data['Start Date'] < current_date + dt.timedelta(days=1))]
        testing = data[(data['Start Date'] >= current_date + dt.timedelta(days=1)) & (data['Start Date'] < current_date + dt.timedelta(days=2))]

        if not training.empty and not testing.empty:
            mean_returns = training.groupby('index').mean()[['Actual Return_breakout', 'Actual Return_OBV', 'Actual Return', 'Actual Return_combined']]

            # Sorting and selecting top stocks
            sorted_by_combined = mean_returns.sort_values('Actual Return_combined', ascending=False)
            selected_stocks = testing[testing['index'].isin(sorted_by_combined.head(10).index)]

            # Calculating the product of returns for the selected stocks
            product = selected_stocks['Actual Return_combined'].prod()
            product_of_returns.append(product)

    except Exception as e:
        print(f"An error occurred on {current_date}: {e}")

    # Move to the next day
    current_date += dt.timedelta(days=1)

# Display the results
print(product_of_returns)


[0.9830692635247437, 1.002343359540813, 1.0132861022293873, 0.966692131202332, 0.9880113544041779, 1.0459039616406625, 0.9943636152284989, 0.9747754654598679, 1.0457945113593128, 1.0370175526955339, 0.9637288687227318, 0.9935724168298666, 0.9759280894955351, 0.9868490286162773, 1.040161058429932, 1.0378488778207027, 0.9919723227500831, 0.9459039837946106, 0.9473955639497467, 1.0233327572110216, 1.3285747564428236, 0.9874788227774521, 0.9766949178058297, 1.0004281076610653, 0.9731396747019592, 0.9371318431881371, 0.9674815360780464, 0.9752574256441828, 1.0187675959537932, 1.0110215811527188]


/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/1392971156.py:18: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  mean_returns = training.groupby('index').mean()[['Actual Return_breakout', 'Actual Return_OBV', 'Actual Return', 'Actual Return_combined']]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/1392971156.py:18: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  mean_returns = training.groupby('index').mean()[['Actual Return_breakout', 'Actual Return_OBV', 'Actual Return', 'Actual Return_combined']]
/var/folders/_s/kwpqd35522v46rqrdqmdzzqh0000gn/T/ipykernel_73579/1392971156.

In [292]:
product_of_returns

[0.9830692635247437,
 1.002343359540813,
 1.0132861022293873,
 0.966692131202332,
 0.9880113544041779,
 1.0459039616406625,
 0.9943636152284989,
 0.9747754654598679,
 1.0457945113593128,
 1.0370175526955339,
 0.9637288687227318,
 0.9935724168298666,
 0.9759280894955351,
 0.9868490286162773,
 1.040161058429932,
 1.0378488778207027,
 0.9919723227500831,
 0.9459039837946106,
 0.9473955639497467,
 1.0233327572110216,
 1.3285747564428236,
 0.9874788227774521,
 0.9766949178058297,
 1.0004281076610653,
 0.9731396747019592,
 0.9371318431881371,
 0.9674815360780464,
 0.9752574256441828,
 1.0187675959537932,
 1.0110215811527188]

In [284]:
sorted_by_combined.head(5).index

Index(['YESBANK.NS', 'ADANIENT.NS', 'HAL.NS', 'ITC.NS', 'INFY.NS'], dtype='object', name='index')

In [157]:
merged_kpi_df[['Actual Return_breakout','Actual Return_OBV','Actual Return','Actual Return_combined']].describe()

Actual Return_breakout  Actual Return_OBV  Actual Return  \
count               50.000000          50.000000      50.000000   
mean                 0.999312           1.003066       0.998836   
std                  0.004588           0.011132       0.004361   
min                  0.980555           0.965947       0.989924   
25%                  0.997874           0.998914       0.995925   
50%                  0.999498           1.001401       0.998460   
75%                  1.000000           1.006241       1.000000   
max                  1.016555           1.047389       1.013040   

       Actual Return_combined  
count               50.000000  
mean                 1.004068  
std                  0.011365  
min                  0.969019  
25%                  0.999146  
50%                  1.001423  
75%                  1.008445  
max                  1.040239

In [164]:
import yfinance as yf
import datetime as dt

# Define the date range
start_loop_date = dt.date(2023, 10, 4)
end_loop_date = dt.date(2023, 10, 5)
current_date = start_loop_date

def is_trading_day(date, ticker="TCS.NS"):
    """
    Check if a specific date was a trading day on the NSE.

    :param date: The date to check (datetime.date or string in 'YYYY-MM-DD' format)
    :param ticker: Ticker symbol to check
    :return: True if it was a trading day, False otherwise
    """
    # Convert date to string if it's a datetime.date object
    if isinstance(date, dt.date):
        date_str = date.strftime('%Y-%m-%d')
    else:
        date_str = date

    # Set end date to one day after start date
    end_date = (dt.datetime.strptime(date_str, '%Y-%m-%d') + dt.timedelta(days=1)).strftime('%Y-%m-%d')

    # Fetch data for the specified date
    data = yf.download(ticker, start=date_str, end=end_date)

    # Check if data is empty
    return not data.empty

# Check if the start date is a trading day
was_trading_day = is_trading_day(current_date)
print(f"Was {current_date} a trading day on NSE? {'Yes' if was_trading_day else 'No'}")


[*********************100%%**********************]  1 of 1 completed
Was 2023-10-04 a trading day on NSE? Yes


In [165]:
was_trading_day

True